In [1]:
import sys
sys.path.append("../")

import csv
import pandas as pd
import numpy as np
import json
from itertools import repeat, chain
import utils
from utils import pad_with_zeros, zeros

In [2]:
data_directory = "data"

## Prep - Scoping to just most populous counties

In [ ]:
# Read the recent populations estimates
population = pd.read_csv(f"{data_directory}/co-est2019-alldata.csv", header=0, encoding='ISO-8859-1')

In [ ]:
# Get counties with population greater than 250K 
pop = population[population['POPESTIMATE2019'] > 100000]

# Filter out entries that are not cities
pop =  pop[pop['CTYNAME'].str.contains('County')]

# Create unique state and place code for merge
pop['STATE_COUNTY'] = pop.apply(lambda x: f"{x['STATE']}:{x['COUNTY']}", axis=1)

# Generate a list of valid states and place
filter_pop = pop['STATE_COUNTY'].to_list()

In [ ]:
# Save the unique state and county pairs that we will be querying from the ACS
with open(f'{data_directory}/state_county.csv', 'w') as f:
    writer = csv.writer(f)
    writer.writerows(list(map(lambda x: x.split(":"), filter_pop)))

## Running

In [ ]:
# Lets set up our requests session. You can use teh creaet session utility or just pass the requests object
session = utils.create_session()

states_and_counties_fp = "{}/state_county.csv".format(data_directory)

# Read in the states and places we will be querying
states_and_counties = pd.read_csv(states_and_counties_fp).values

In [ ]:
states_and_counties[:10].shape

In [ ]:
codes = {'acs/acs5':[ "B01003_001E", "B01002_002E", "B01002_001E", "B02001_002E", "B06009_001E",
                    "B06009_002E", "B06009_003E", "B06009_005E", "B06009_006E"],
        'acs/acs5/profile' : ["DP02_0001E", "DP04_0037E", "DP03_0062E"]} #TODO #All missing "B06011_001E"
acs_endpoints = ['acs/acs5', 'acs/acs5/profile']


df = utils.gather_results(session, acs_endpoints, utils.config, states_and_counties, codes, dfs=[], start=0)


In [ ]:
df.columns

In [ ]:
df.to_csv("census_tracts.csv", index= False)

In [ ]:
df.shape

## Merging Data by Tract

In [34]:
census_tracts = pd.read_csv("census_tracts.csv")
census_tracts.shape

(54450, 16)

In [36]:
#Some of the data needs a geoid
#GEOID is defined as: STATE+COUNTY+TRACT
#See: https://www.census.gov/programs-surveys/geography/guidance/geo-identifiers.html
def create_geoid(row):
    geoid = str(utils.pad_with_zero(row["state"])) + str(utils.pad_place_with_zero(row["county"])) + str(utils.pad_tract_with_zero(row["tract"]))
    return int(geoid)

census_tracts["GEOID"] = census_tracts.apply(create_geoid, axis=1)

### Other data files

In [37]:
census_tracts.shape

(54450, 17)

In [5]:
land_area = pd.read_csv("data/2021_Gaz_tracts_national.txt", sep="\t")
land_area

USPS        GEOID     ALAND  AWATER  ALAND_SQMI  AWATER_SQMI   INTPTLAT  \
0       AL   1001020100   9825304   28435       3.794        0.011  32.481973   
1       AL   1001020200   3320818    5669       1.282        0.002  32.475758   
2       AL   1001020300   5349271    9054       2.065        0.003  32.474024   
3       AL   1001020400   6384282    8408       2.465        0.003  32.471030   
4       AL   1001020501   6203654       0       2.395        0.000  32.447861   
...    ...          ...       ...     ...         ...          ...        ...   
85390   PR  72153750501   1820185       0       0.703        0.000  18.031211   
85391   PR  72153750502    689931       0       0.266        0.000  18.024746   
85392   PR  72153750503   3298433    1952       1.274        0.001  18.023148   
85393   PR  72153750601  10985103    4527       4.241        0.002  18.017809   
85394   PR  72153750602  17522417  252953       6.765        0.098  17.985025   

       INTPTLONG                                                                                                                               
0                                             -86.491565                                                                                       
1                                             -86.472468                                                                                       
2                                             -86.459703                                                                                       
3                                             -86.444835                                                                                       
4                                             -86.422558                                                                                       
...                                                  ...                                                                                       
85390                                         -66.867347                                                                                       
85391                                         -66.860442                                                                                       
85392                                         -66.876603                                                                                       
85393                                         -66.839070                                                                                       
85394                                         -66.853531                                                                                       

[85395 rows x 8 columns]

In [6]:
census_tracts["GEOID"]

0         1015002000
1         1015000800
2         1015000900
3         1015001400
4         1015002102
            ...     
54445    55139001400
54446    55139003400
54447    55139001100
54448    55139002000
54449    55139002100
Name: GEOID, Length: 54450, dtype: int64

In [20]:
tracts_with_land = census_tracts.merge(land_area[["GEOID","ALAND", "ALAND_SQMI"]], how = "left", on = "GEOID")
tracts_with_land.shape

(54450, 19)

In [26]:
sum(pd.isna(tracts_with_land["ALAND"])) #8421 Trues where ALAND is NA

8421

In [27]:
pd.set_option('display.max_rows', None)
tracts_with_land[pd.isna(tracts_with_land["ALAND"])][["NAME", "state","county", "GEOID", "tract"]]

NAME  state  county  \
0               Census Tract 20, Calhoun County, Alabama      1      15   
10           Census Tract 21.03, Calhoun County, Alabama      1      15   
11           Census Tract 25.01, Calhoun County, Alabama      1      15   
15              Census Tract 18, Calhoun County, Alabama      1      15   
16              Census Tract 11, Calhoun County, Alabama      1      15   
29              Census Tract 15, Calhoun County, Alabama      1      15   
34           Census Tract 105.01, Etowah County, Alabama      1      55   
44           Census Tract 105.02, Etowah County, Alabama      1      55   
51              Census Tract 102, Etowah County, Alabama      1      55   
61          Census Tract 402.02, Houston County, Alabama      1      69   
71             Census Tract 419, Houston County, Alabama      1      69   
74             Census Tract 408, Houston County, Alabama      1      69   
80          Census Tract 402.01, Houston County, Alabama      1      69   
91        Census Tract 111.11, Jefferson County, Alabama      1      73   
93        Census Tract 113.02, Jefferson County, Alabama      1      73   
96        Census Tract 123.05, Jefferson County, Alabama      1      73   
100       Census Tract 128.03, Jefferson County, Alabama      1      73   
103       Census Tract 129.12, Jefferson County, Alabama      1      73   
106       Census Tract 129.15, Jefferson County, Alabama      1      73   
113       Census Tract 144.13, Jefferson County, Alabama      1      73   
120       Census Tract 106.02, Jefferson County, Alabama      1      73   
122       Census Tract 117.03, Jefferson County, Alabama      1      73   
132           Census Tract 24, Jefferson County, Alabama      1      73   
141       Census Tract 111.04, Jefferson County, Alabama      1      73   
163       Census Tract 117.05, Jefferson County, Alabama      1      73   
166       Census Tract 141.02, Jefferson County, Alabama      1      73   
167       Census Tract 142.03, Jefferson County, Alabama      1      73   
168       Census Tract 143.02, Jefferson County, Alabama      1      73   
177       Census Tract 142.04, Jefferson County, Alabama      1      73   
187       Census Tract 108.05, Jefferson County, Alabama      1      73   
189          Census Tract 114, Jefferson County, Alabama      1      73   
192       Census Tract 129.06, Jefferson County, Alabama      1      73   
203       Census Tract 120.02, Jefferson County, Alabama      1      73   
212       Census Tract 118.02, Jefferson County, Alabama      1      73   
216           Census Tract 45, Jefferson County, Alabama      1      73   
221           Census Tract 27, Jefferson County, Alabama      1      73   
231       Census Tract 111.07, Jefferson County, Alabama      1      73   
242       Census Tract 110.01, Jefferson County, Alabama      1      73   
246                Census Tract 418, Lee County, Alabama      1      81   
247                Census Tract 402, Lee County, Alabama      1      81   
250                Census Tract 419, Lee County, Alabama      1      81   
252                Census Tract 417, Lee County, Alabama      1      81   
256             Census Tract 406.04, Lee County, Alabama      1      81   
259             Census Tract 420.04, Lee County, Alabama      1      81   
260             Census Tract 409.02, Lee County, Alabama      1      81   
264             Census Tract 421.02, Lee County, Alabama      1      81   
266                Census Tract 405, Lee County, Alabama      1      81   
269                Census Tract 404, Lee County, Alabama      1      81   
270                Census Tract 408, Lee County, Alabama      1      81   
271                Census Tract 410, Lee County, Alabama      1      81   
272                Census Tract 411, Lee County, Alabama      1      81   
275            Census Tract 113, Madison County, Alabama      1      89   
280            Census Tract 101, Madison County, Alabama      1      89   
28

In [ ]:
#This is by block group so may need to align on whether to average or not?
epa = pd.read_csv("data/EPA_SmartLocationDatabase_V3_Jan_2021_Final.csv")
epa

In [32]:
schools = pd.read_excel("data/grf20_lea_tract.xlsx")
schools.rename(columns={"TRACT" : "GEOID"}, inplace=True)
schools[:10]

LEAID                        NAME_LEA20       GEOID  COUNT   LANDAREA  \
0  100001       Fort Rucker School District  1031010300      2  23.428369   
1  100001       Fort Rucker School District  1045020000      2  66.513404   
2  100003       Maxwell AFB School District  1101000900      2   3.356590   
3  100003       Maxwell AFB School District  1101001000      2   0.001526   
4  100005  Albertville City School District  1095030701      9   2.125782   
5  100005  Albertville City School District  1095030702      9   0.800890   
6  100005  Albertville City School District  1095030801      9   5.460084   
7  100005  Albertville City School District  1095030803      9   1.399229   
8  100005  Albertville City School District  1095030804      9   3.900132   
9  100005  Albertville City School District  1095030902      9   7.294520   

   WATERAREA  
0   0.000000  
1   1.081745  
2   0.143795  
3   0.000000  
4   0.000000  
5   0.009930  
6   0.012075  
7   0.005014  
8   0.012770  
9   0.033274

In [38]:
tracts_with_schools = census_tracts.merge(schools, how = "left", on = "GEOID")
tracts_with_schools.shape

(71575, 22)

In [42]:
np.unique(tracts_with_schools["GEOID"]).shape

(54450,)

In [43]:
tracts_with_schools["GEOID"].value_counts()

36103990100    32
6081990100     17
6019007600     14
6097154304     14
6023010902     13
6023001200     13
6053011400     13
6107004200     12
6083990000     12
6029004500     12
17099962200    11
6029003304     11
25009990100    11
17099964100    11
6041990100     11
6031000100     11
17099962300    11
6001990000     10
30031000400    10
6053010606     10
6031001200     10
36103159510    10
6073990100     10
17019010400    10
17099964000    10
6041133000     10
30031001200     9
6047001901      9
40017300100     9
6085511707      9
4025001402      9
6111000500      9
25001990000     9
6089012400      9
6085513500      9
17031820202     9
6025012301      9
6071009202      9
6023011100      9
30111001402     9
6023010300      9
30031000300     9
6039000109      9
6097151100      9
55127001702     9
6041131100      9
6047000901      9
6023001300      9
30029000602     9
6107002100      9
6029003900      9
6079013000      9
30029000601     9
40017300202     9
17019010604     9
5307794000